<a href="https://colab.research.google.com/github/rendalamili/ml-for-table-extraction/blob/main/Camelot_and_Machine_Learning.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Resources

https://huggingface.co/transformers/v4.3.3/_modules/transformers/training_args.html#:~:text=[docs]%20@dataclass%20class%20TrainingArguments:%20%22%22%22%20TrainingArguments%20is%20the%20subset%20of

https://github.com/NielsRogge/Transformers-Tutorials/blob/master/Table%20Transformer/Using_Table_Transformer_for_table_detection_and_table_structure_recognition.ipynb

https://pytorch.org/tutorials/beginner/blitz/tensor_tutorial.html?highlight=cuda#cuda-tensors

https://github.com/microsoft/table-transformer/blob/main/docs/INFERENCE.md

https://camelot-py.readthedocs.io/en/master/

https://github.com/tesseract-ocr/tesseract

https://www.kaggle.com/datasets/sreesankar711/pubtables-subset-100k

https://github.com/microsoft/table-transformer

In [1]:
# Install packages
#%pip install camelot-py[cv] ghostscript PyPDF2==1.26.0 pdf2image transformers matplotlib numpy opencv-python pandas torch tensorflow table-transformer datasets timm
#!apt-get install -y ghostscript
#%pip install --upgrade camelot-py[cv]
#%pip install pytesseract
#%pip install kaggle
#!apt-get install -y tesseract-ocr
#!apt-get install -y poppler-utils
#!pip install --upgrade pillow datasets
#!kaggle datasets download -d sreesankar711/pubtables-subset-100k
#!unzip pubtables-subset-100k.zip -d C:\Users\Osama\Downloads\ml-for-table-extraction\content\pubtables



Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.1.2 -> 24.2
[notice] To update, run: python.exe -m pip install --upgrade pip
'apt-get' is not recognized as an internal or external command,
operable program or batch file.


  Using cached camelot_py-0.11.0-py3-none-any.whl.metadata (8.3 kB)
  Using cached pypdf-5.0.1-py3-none-any.whl.metadata (7.4 kB)
  Using cached tabulate-0.9.0-py3-none-any.whl.metadata (34 kB)
INFO: pip is looking at multiple versions of camelot-py[cv] to determine which version is compatible with other requirements. This could take a while.
  Using cached camelot_py-0.10.1-py3-none-any.whl.metadata (8.3 kB)
  Using cached camelot_py-0.10.0-py3-none-any.whl.metadata (8.3 kB)
Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.1.2 -> 24.2
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.1.2 -> 24.2
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.1.2 -> 24.2
[notice] To update, run: python.exe -m pip install --upgrade pip
'apt-get' is not recognized as an internal or external command,
operable program or batch file.
'apt-get' is not recognized as an internal or external command,
operable program or batch file.


In [2]:
# Import libraries
import os
import json
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

In [3]:
# PDF libaries
import camelot
import ghostscript
import PyPDF2 as pypdf
from pdf2image import convert_from_path

In [4]:
# Image processsing libaries
import pytesseract
import cv2
import PIL
from PIL import Image
from PyPDF2 import PdfFileReader

In [5]:
# Pytorch libraries
import torch
from torch.utils.data import DataLoader
from torchvision import datasets, transforms
from torchvision.datasets import ImageFolder

In [6]:

# Transformer and datasets
import transformers
from transformers import TableTransformerForObjectDetection, pipeline
from transformers import AutoImageProcessor
from transformers import DefaultDataCollator
# Issue importing trainer 
# from transformers import Trainer, TrainingArguments, default_data_collator
import datasets
from datasets import load_dataset
from datasets import Dataset, Features, ClassLabel, Value, Image as ImageType

# Google Collab
# from google.colab import files



c:\Users\Osama\Downloads\ml-for-table-extraction\myenv\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [7]:
# Specify the path to your PDF file
pdf_file = r"C:\Users\Osama\Downloads\ml-for-table-extraction\Tables\1_simple_table.pdf"


# Make sure the file exists
if not os.path.exists(pdf_file):
    raise FileNotFoundError(f"The file {pdf_file} does not exist.")

print(f"Using PDF file: {pdf_file}")

Using PDF file: C:\Users\Osama\Downloads\ml-for-table-extraction\Tables\1_simple_table.pdf


In [9]:
def extract_pdf_table(pdf_file):
    # Initialise tables list to store extracted tables
    tables = []

    # Extract tables using Camelot (stream)
    try:
        tables = camelot.read_pdf(pdf_file, pages='all', flavor='stream')
    except Exception as e:
        print(f"Error extracting table with Camelot (stream): [{e}]")
        # Extract using Camelot (lattice)
        try:
            tables = camelot.read_pdf(pdf_file, pages='all', flavor='lattice')
        except Exception as e:
            print(f"Error extracting table with Camelot (lattice): [{e}]")

    # If tables were sucessfully extracted using Camelot, return them
    if tables:
        print(f"Extracted {len(tables)} tables using Camelot.")
        return [table.df.values.tolist() for table in tables]

    # If Camelot was unsucessful use OCR
    print("Using OCR for image-based table extraction.")

    # Convert PDF to image using pdf2image
    images = convert_from_path(pdf_file, poppler_path=r"C:\poppler-24.08.0\Library\bin", fmt='png') # Change poppler_path for your machine

    # Initialise list to store extracted text from images
    extract_text_table = []

    pytesseract.pytesseract.tesseract_cmd = r'C:\Program Files\Tesseract-OCR\tesseract.exe'  # Adjust this path as needed 

    # Extract text from images using Tesseract
    for i, image in enumerate(images):
      image = image = image.convert('RGB')
      text = pytesseract.image_to_string(image)
      extract_text_table.append(text)
      print(f"Extracted text from image [{i + 1}/{len(images)}]")

    # Process extracted text into structured data
    extracted_data = []
    for text in extract_text_table:
        rows = text.split('\n')  # Split text into rows
        for row in rows:
            if row.strip():  # Ignore empty rows
                extracted_data.append(row.strip().split())  # Split into columns

    return extracted_data  # Return structured data

    #upload = files.upload()
    #pdf_file = list(upload.keys())[0]

# Example use of extract_pdf_table function
if __name__ == "__main__":
    data = extract_pdf_table(pdf_file)
    print(data)

Error extracting table with Camelot (stream): [Could not find xref table at specified location]
Error extracting table with Camelot (lattice): [Could not find xref table at specified location]
Using OCR for image-based table extraction.
Extracted text from image [1/1]
[['Header', '1', 'Header', '3'], ['Row', '1,', 'Col', '1', '|', 'Row', '1,', 'Col', '2', '|', 'Row', '1,', 'Col', '3'], ['Row', '2,', 'Col', '1', '|', 'Row', '2,', 'Col', '2', '|', 'Row', '2,', 'Col', '3'], ['Row', '3,', 'Col', '1', '|', 'Row', '3,', 'Col2', '|', 'Row', '3,', 'Col', '3'], ['Row', '4,', 'Col', '1', '|', 'Row', '4,', 'Col', '2', '|', 'Row', '4,', 'Col', '3']]


In [10]:
# Convert table to JSON
def json_table(table):
  # Check if table has DataFrame 'df' attribute
  if hasattr(table, 'df'):
    header = table.df.values.tolist() # Get df header
    rows = table.df.values.tolist() # Get df rows
    # Return list of dictionaries
    return [dict(zip(header, row)) for row in rows]
  else:
    # If table is a list or tuple
    if table and isinstance(table, (list, tuple)) and len(table) > 1:
      header = table[0] # First element is header
      rows = table[1:] # Remaining elements are rows
      # Return list of dictionaries
      return [dict(zip(header, row)) for row in rows]
    else:
      print("Invalid table format for JSON conversion.")
      return []


In [11]:
# Extract table from PDF file and store as tables
tables = extract_pdf_table(pdf_file)

# Convert extracted table to JSON
json_tables = [json_table(table) for table in tables]
with open('tables.json', 'w') as f:
  json.dump(json_tables, f)

Error extracting table with Camelot (stream): [Could not find xref table at specified location]
Error extracting table with Camelot (lattice): [Could not find xref table at specified location]
Using OCR for image-based table extraction.
Extracted text from image [1/1]


In [12]:
# Convert extracted table to an image
for i, table in enumerate(tables):
  df = pd.DataFrame(table)

  # Create new figure and axis for plotting
  fig, ax = plt.subplots()
  ax.axis('off')

  # Create table plot with DataFrame values and column labels
  plot_table = ax.table(cellText=df.values, colLabels=df.columns, loc='center')

  # Save plot as PNG image
  plt.savefig(f'table_{i}.png', bbox_inches='tight', pad_inches=0)
  plt.close()

In [13]:
# Load pre-trained Table Transformer model
model = TableTransformerForObjectDetection.from_pretrained('microsoft/table-transformer-detection')

c:\Users\Osama\Downloads\ml-for-table-extraction\myenv\lib\site-packages\huggingface_hub\file_download.py:147: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\Osama\.cache\huggingface\hub\models--microsoft--table-transformer-detection. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)
c:\Users\Osama\Downloads\ml-for-table-extraction\myenv\lib\site-packages\hug

In [ ]:
# Load image processor
image_processor = AutoImageProcessor.from_pretrained("microsoft/table-transformer-detection")

preprocessor_config.json:   0%|          | 0.00/273 [00:00<?, ?B/s]

The `max_size` parameter is deprecated and will be removed in v4.26. Please specify in `size['longest_edge'] instead`.


In [ ]:
# Load training dataset
train_dataset = load_dataset('imagefolder', data_dir='/content/pubtables/subset/img_train')

# Load validation dataset
#val_dataset = load_dataset('imagefolder', data_dir='/content/pubtables/subset/img_val')

Resolving data files:   0%|          | 0/60000 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

In [ ]:
# Test dataset
print(train_dataset['train'][0])

{'image': <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=643x149 at 0x7B5FBED931C0>}


In [ ]:
# Subset of 100 examples from the training dataset
subset_training_dataset = train_dataset['train'].select(range(100))

In [ ]:
def preprocess_function(examples):
    # Define transformations
    transform = transforms.Compose([
        transforms.Resize((224, 224)), # Resize image
        transforms.ToTensor(),         # Convert image to Pytorch tensor
        transforms.Normalize(mean=[0.5, 0.5, 0.5], std=[0.5, 0.5, 0.5]) # Normalise pixel value
    ])

    # Find colum in dataset that contains image paths or image objects
    image_column = 'image_path'
    if image_column not in examples:
        image_column = 'image'  # Fallback to 'image' column
        if image_column not in examples:
            raise KeyError(f"Neither 'image_path' nor 'image' found in the dataset columns: {list(examples.keys())}")

    if 'pixel_values' in examples:
        return examples

    # Initialise 'pixel_values' as tensor list
    examples['pixel_values'] = []

    # Check image objects
    for image in examples[image_column]:
        try:
            # If PIL Image, convert to RGB
            pil_image = image.convert("RGB")
            # Apply transformations
            examples['pixel_values'].append(transform(pil_image))
        except (TypeError, ValueError, IOError, AttributeError) as e:
            print(f"Error processing image: {e}, type: {type(image)}")
            examples['pixel_values'].append(torch.zeros(3, 224, 224))  # Placeholder

    # Convert list of tensors to single tensor
    examples['pixel_values'] = torch.stack(examples['pixel_values'])

    return examples

In [ ]:
# Apply preprocessing function to the subset dataset
subset_training_dataset = subset_training_dataset.map(preprocess_function, batched=True)

# Apply preprocessing to the training dataset
#train_dataset = train_dataset.map(preprocess_function, batched=True)
# Apply preprocessing to the validation dataset
#val_dataset = val_dataset.map(preprocess_function, batched=True)

Map:   0%|          | 0/100 [00:00<?, ? examples/s]

In [ ]:
# Test preprocessing
print(subset_training_dataset[0])

{'image': <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=643x149 at 0x7AEFE0B87970>, 'pixel_values': [[[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.9607843160629272, 0.9450980424880981, 0.9372549057006836, 0.9529411792755127, 0.9764705896377563, 0.9529411792755127, 0.9372549057006836, 0.9529411792755127, 0.9529411792755127, 0.9529411792755127, 0.9686274528503418, 0.9921568632125854, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0

In [ ]:
# Prepare batch for training
def custom_data_collator(features):
    # Initialise dictionary to hold batch data
    batch = {}

    # Stack pixel value into tensor
    batch['pixel_values'] = torch.stack([f['pixel_values'] for f in features])

    # Handle labels
    if 'labels' in features[0]:
        batch['labels'] = [f['labels'] for f in features]

    return batch

In [ ]:
# Test dataset
print(subset_training_dataset[0])

{'image': <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=643x149 at 0x7AEFE0B85870>, 'pixel_values': [[[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.9607843160629272, 0.9450980424880981, 0.9372549057006836, 0.9529411792755127, 0.9764705896377563, 0.9529411792755127, 0.9372549057006836, 0.9529411792755127, 0.9529411792755127, 0.9529411792755127, 0.9686274528503418, 0.9921568632125854, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0

In [ ]:
# Test dataset
print(type(subset_training_dataset['pixel_values'][0]))

<class 'list'>


In [ ]:
# Training arguments
training_arguments = TrainingArguments(
    output_dir='./results',                    # Model prediction directory
    evaluation_strategy='epoch',               # Evaluation strategy during training
    save_strategy='epoch',                     # Save strategy during training
    save_total_limit=2,                        # Maximum number of checkpoints to save
    save_steps=100,                            # Save every 100 steps
    learning_rate=2e-5,                        # Learning rate
    per_device_train_batch_size=16,            # Training batch size
    per_device_eval_batch_size=16,             # Evaluation batch size
    num_train_epochs=3,                        # Training epochs
    logging_dir='./logs',                      # Logging directory
    logging_steps=10,                          # Log training
    remove_unused_columns=False,               # Do not remove unused columns in dataset
)

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [ ]:
# Initialise Trainer for model training
trainer = Trainer(
    model=model,                               # Trained model
    args=training_arguments,                   # Training arguments
    train_dataset=train_dataset['train'],      # Training dataset
    data_collator=custom_data_collator         # Data collator for batch
    #eval_dataset=val_dataset['train'],        # Training validation data set
)

In [ ]:
# Train model
trainer.train()

KeyError: 'pixel_values'

In [ ]:
# Test image on model
table_recogniser = pipeline('table-recognition', model=model)

# Load table image
test_image = Image.open('table_0.png')
table_recogniser(test_image)

# Convert prediction to JSON
predicted_tables = json.dumps(table_recogniser(test_image))
with open('predicted_tables.json', 'w') as f:
  f.write(predicted_tables)

print(prediction_json)

KeyError: "Unknown task table-recognition, available tasks are ['audio-classification', 'automatic-speech-recognition', 'depth-estimation', 'document-question-answering', 'feature-extraction', 'fill-mask', 'image-classification', 'image-feature-extraction', 'image-segmentation', 'image-to-image', 'image-to-text', 'mask-generation', 'ner', 'object-detection', 'question-answering', 'sentiment-analysis', 'summarization', 'table-question-answering', 'text-classification', 'text-generation', 'text-to-audio', 'text-to-speech', 'text2text-generation', 'token-classification', 'translation', 'video-classification', 'visual-question-answering', 'vqa', 'zero-shot-audio-classification', 'zero-shot-classification', 'zero-shot-image-classification', 'zero-shot-object-detection', 'translation_XX_to_YY']"